## <font color='DeepSkyBlue'>Postprocessing pyWaPOR outputs</font>
After successfully running pyWaPOR, you will get the result in netCDF file format. You can use the **xarray**, **rioxarray** and **geopandas** python packages to postprocess the result, extract the information you may like to include in a report or present the results for non-experts in the format they can easily understand such as maps, tables, etc.    
You can, for example, do the following:
* clip the dataset using a shapefile of your area of interest
* calculate timeseries of the variables for your area of interest
* calculate statistics of the dataset and many more

#### Step 0: Import required packages

In [ ]:
import xarray as xr
import rioxarray as rio
import geopandas as gpd
import matplotlib.pyplot as plt
from matplotlib.animation import FuncAnimation
from mpl_toolkits.axes_grid1 import make_axes_locatable
import os

#### Step 1: Read pywapor output

In [ ]:
# Set paths

# Kenya
path_et_look_out = r""
path_aoi_shape = r""
out_put_dir = r''

# Create output directory if doesn't exist
if not os.path.exists(out_put_dir):
    os.makedirs(out_put_dir)

# Read the et_look output netCDF file
ds = xr.open_dataset(path_et_look_out, decode_coords="all")
if('time_bins' in ds.dims):
    ds = ds.rename({'time_bins': 'time'})

# read the shapefile using geopandas
shapefile = gpd.read_file(path_aoi_shape)

# Make sure the dataset has spatial information (crs). The output files have CRS EPSG:4326
ds = ds.rio.write_crs("EPSG:4326")  # Modify with appropriate CRS if needed

# Ensure the shapefile has the same CRS as the dataset
shapefile = shapefile.to_crs(ds.rio.crs)

In [ ]:
# Explore the dataset
ds

In [ ]:
# plot the aeti for one time step
ds.aeti_24_mm[37].plot()

#### Step 2: Select the data for a season and clip the dataset using the shapefile

In [ ]:
#Specify the start and end dates of the season
season = ["2023-05-01", "2023-12-31"] # Kenya

# select the data for the season
dss = ds.sel(time=slice(season[0], season[1]))

# Clip the data using the shapefile 
clipped_ds = dss.rio.clip(shapefile.geometry, shapefile.crs, drop = True)

# replace negative values by zero, if there are any
clipped_ds = clipped_ds.where((clipped_ds>=0.0) | clipped_ds.isnull(), 0.0)

In [ ]:
# Explore the clipped dataset
clipped_ds

#### Step 3: Use the clipped dataset to compute some statistics
For example;
* Statistics of monthly AETI, I, T, E and RSM and Biomass Production over the study area.  
* Temporal variation of daily AETI and Biomass Production for the study area 

In [ ]:
# Compute temporal variation (e.g., daily variation)
daily_mean = clipped_ds.mean(dim=['y', 'x'], skipna=True, keep_attrs=True)

# Compute monthly statistics
# monthly means
monthly_mean = clipped_ds.resample(time='ME').mean(dim='time', skipna=True)

# monthly sum
monthly_sum = clipped_ds.resample(time='ME').sum(dim='time', skipna=True)+0*monthly_mean

# update unit
_ = [monthly_sum[var].attrs.update({'units': 'mm/month'}) for var in monthly_sum.data_vars]

# Compute monthly standard deviation
monthly_std = clipped_ds.resample(time='ME').std(dim='time')

#### Step 4: Make some plots.
You can produce maps (like what you can do using QGIS), timeseries plots and barcharts.

One nice thing of working with netCDF files (files with .nc extension) and opening them in xarray is that we have access to a number of simple plotting methods. For example, if you simply add *.plot()*, to your dataset a default plot for the type of data will be created.    
<br>
These plots are:
- for 3 dimensional data (time, x, y): a histogram
- for 2 dimensional data (x,y): a map
- for 1 dimensional data (time): a line plot <br>

Let us start by looking at *monthly_sum.aeti_24_mm*

In [ ]:
monthly_sum.aeti_24_mm.plot();
#This data has 3 dimensions: time, x and y. The plot is therefore a histogram.

In [ ]:
monthly_mean.aeti_24_mm[0].plot();
#This data has 2 dimensions: x and y. For time we have selected the 1st timestep with the selection [0]

In [ ]:
monthly_sum.aeti_24_mm.mean(dim=['y', 'x']).plot(); 
# Here we are performing the spatial averaging with .mean(dim=['y', 'x']) - so we are left with a 1d timeseries.

In [ ]:
# Similarly the daily values
daily_mean.aeti_24_mm.plot()

#### Step 5: Make some fancier plots.
You can produce nicer maps (like what you can do using QGIS), timeseries plots and barcharts - these are examples of how you can control the layout, font, color etc of your plots.

In [ ]:
def plot_map(da, boundary, fig_title, var_label_and_unit, save_folder):
    """
    Plots a spatial map of data with a boundary overlay and saves the figure.
    
    Parameters:
        da (xarray.DataArray): The data array to be plotted.
        boundary (geopandas.GeoDataFrame): The boundary shapefile to overlay.
        fig_title (str): Title of the figure.
        var_label_and_unit (str): Label for the colorbar.
        save_folder (str): Directory to save the output figure.
    """
    fig, ax = plt.subplots(figsize=(6, 6))
    ax.set_aspect(1)

    # Plot the data using pcolormesh
    p = da.plot.pcolormesh(ax=ax, add_colorbar=False)
    
    # Add the boundary (shapefile outline) to the plot
    boundary.plot(ax=ax, edgecolor='red', color='none')

    # Set plot margins with a small buffer
    xmin, xmax = da.x.min().data, da.x.max().data
    ymin, ymax = da.y.min().data, da.y.max().data
    mf = 0.05  # Margin factor
    ax.set_xlim((1+mf)*xmin - mf*xmax, (1+mf)*xmax - mf*xmin)
    ax.set_ylim((1+mf)*ymin - mf*ymax, (1+mf)*ymax - mf*ymin)
  
    # Set the title and axis labels
    ax.set_title(fig_title)
    ax.set_xlabel('Longitude')
    ax.set_ylabel('Latitude')

    # Add a separate colorbar
    divider = make_axes_locatable(ax)
    cax1 = divider.append_axes("right", size="5%", pad=0.05)
    cbar = plt.colorbar(p, cax=cax1)
    cbar.set_label(var_label_and_unit)
    
    plt.tight_layout()  
    
    # Save the figure as a PNG file
    plt.savefig(os.path.join(save_folder, f'{fig_title}.png'), dpi=600)

def time_series_plot(da, fig_title, var_label_and_unit, save_folder):
    """
    Plots a time series of data and saves the figure.
    
    Parameters:
        da (xarray.DataArray): The data array containing time series data.
        fig_title (str): Title of the figure.
        var_label_and_unit (str): Label for the y-axis.
        save_folder (str): Directory to save the output figure.
    """
    fig, ax = plt.subplots(figsize=(6, 3))
    
    # Plot the time series data
    da.plot(ax=ax)
    
    # Set the title and axis labels
    ax.set_title(fig_title)
    ax.set_ylabel(var_label_and_unit)
    ax.set_xlabel('Time')
    
    plt.tight_layout()  
    
    # Save the figure as a PNG file
    plt.savefig(os.path.join(save_folder, f'{fig_title}.png'), dpi=600)

def plot_bar(df, fig_title, var_type, unit, save_folder):
    """
    Plots a bar chart from a DataFrame and saves the figure.
    
    Parameters:
        df (pandas.DataFrame): The data frame containing the bar chart values.
        fig_title (str): Title of the figure.
        var_type (str): Type of variable to be plotted.
        unit (str): Unit of measurement for the variable.
        save_folder (str): Directory to save the output figure.
    """
    fig, ax = plt.subplots(figsize=(8, 4))
    
    # Plot bar chart with specified rotation and width
    ax = df.plot.bar(rot=0, width=0.85, figsize=(6, 3))
    
    # Add grid lines for better readability
    ax.grid(visible=True, which='major', color='0.4', linestyle='--', linewidth=0.25, zorder=0)
    
    # Set the title and axis labels
    ax.set_title(fig_title)
    ax.set_xlabel("Month")
    ax.set_ylabel(f'{var_type} {unit}')
    
    # Rotate x-axis labels for better readability
    plt.xticks(rotation=45)
    
    plt.tight_layout()
    
    # Save the figure as a PNG file
    plt.savefig(os.path.join(save_folder, f'{fig_title}.png'), dpi=600)

In [ ]:
# set axes and font globally
font = {'style' : 'normal', 'family':'sans-serif'}
axes ={'titlesize':14, 'labelsize':'small', 'labelcolor': 'steelblue'}
plt.rc('font', **font)
plt.rc('axes', **axes)
plt.rcParams['text.color'] = 'steelblue'

# # Plot monthly maps
da = monthly_sum.aeti_24_mm[0] # Select data of 1 timestep, 0 indicates the first timestep in this case
time = da.time.dt.strftime('%b %Y').values
name = da.name.split('_')[0].upper()
unit = da.attrs['units']
fig_title =f"Total {name} for {time}"
var_label_and_unit = f"{name} {unit}"
plot_map(da, shapefile, fig_title, var_label_and_unit, out_put_dir)

# timeseries plot
ts = daily_mean.aeti_24_mm
name = ts.name.split('_')[0].upper()
unit = 'mm/day'
fig_title =f"Spatially Averaged Daily {name} "
var_label_and_unit = f"{name} {unit}"
time_series_plot(ts, fig_title, var_label_and_unit, out_put_dir)


#bar plot
mn_mean = daily_mean.resample(time='ME').mean(dim='time')
mn_mean['time'] = mn_mean['time'].dt.strftime('%b %Y')
df = mn_mean.aeti_24_mm.to_series()
name = df.name.split('_')[0].upper()
fig_title =f"Monthly Mean {name} "
var_label = 'Monthly ET'
unit = 'mm/day'
plot_bar(mn_mean.aeti_24_mm.to_series(),fig_title, var_label, unit, out_put_dir)


#### Step 6: You can alos make animation of the mpas.
You can produce animation in gif format or movie of the maps. An example si shown below.

In [ ]:
# Create animation of ET (Evapotranspiration) maps

# Select the variable to plot from the dataset
data = clipped_ds.aeti_24_mm  # Extract ET data
vmin = data.min().values.round(1)  # Get the minimum value and round it
vmax = data.max().values.round(1)  # Get the maximum value and round it

# Initialize the figure and axis for plotting
fig, ax = plt.subplots(figsize=(6, 6))
ax.set_aspect(1)  # Maintain aspect ratio

# Set up initial frame (first time step)
cmap = 'Reds'  # Define the colormap
p = data.isel(time=0).plot.pcolormesh(ax=ax, cmap=cmap, animated=True, 
                                      add_colorbar=False, vmin=vmin, vmax=vmax)

# Add the boundary from the shapefile
shapefile.plot(ax=ax, edgecolor='black', color='none')

# Set plot margins
xmin, xmax = da.x.min().data, da.x.max().data
ymin, ymax = da.y.min().data, da.y.max().data
mf = 0.05  # Margin factor for expanding axis limits
ax.set_xlim((1+mf) * xmin - mf * xmax, (1+mf) * xmax - mf * xmin)
ax.set_ylim((1+mf) * ymin - mf * ymax, (1+mf) * ymax - mf * ymin)

# Set the title and axis labels
ax.set_title(fig_title)
ax.set_xlabel('Longitude')
ax.set_ylabel('Latitude')

# Add a separate colorbar
divider = make_axes_locatable(ax)
cax1 = divider.append_axes("right", size="5%", pad=0.05)  # Position the colorbar
cbar = plt.colorbar(p, cax=cax1)  # Create the colorbar
cbar.set_label(var_label_and_unit)  # Set the label for the colorbar
plt.tight_layout()  # Adjust layout to fit everything nicely

# Function to update each frame in the animation
def update(i):
    ax.clear()  # Clear the previous frame
    
    # Update the plot with new time step
    p = data.isel(time=i).plot.pcolormesh(ax=ax, cmap=cmap, animated=True, add_colorbar=False)
    
    # Re-add the boundary (to avoid it being removed after clearing the frame)
    shapefile.plot(ax=ax, edgecolor='black', color='none')
    
    # Update the title with the current date
    ax.set_title(f'Date: {data.time.dt.strftime("%d-%m-%Y").values[i]}')
    
    plt.tight_layout()  # Ensure layout stays clean
    return p,

# Create the animation
ani = FuncAnimation(fig, update, frames=len(data.time), interval=1000, blit=True)

# Show the animation
plt.show()

# Save as an animation file (optional)
fig_title = 'ET_animation_3m'
ani.save(os.path.join(out_put_dir, f'{fig_title}.gif'), fps=1, dpi=600, writer='imagemagick')
